In [99]:
import pandas as pd
import numpy as np
import plotly
import plotly.express as px
import chart_studio.plotly as py
import chart_studio
import matplotlib.pyplot as plt

chart_studio.tools.set_credentials_file(username='oystein.nerva', api_key='0ODcZ6UisJ8n0AjEQt9N')

In [100]:
# finn API url her: https://data.ssb.no/api/v0/dataset

url = "https://data.ssb.no/api/v0/dataset/1078.csv?lang=no"

df = pd.read_csv(url, sep=";", decimal=",", encoding="ISO-8859-1")
df.head()

region   kjønn            alder    år statistikkvariabel  \
0  3001 Halden  1 Menn    F00-04 0-4 år  2020           Personer   
1  3001 Halden  1 Menn    F05-09 5-9 år  2020           Personer   
2  3001 Halden  1 Menn  F10-14 10-14 år  2020           Personer   
3  3001 Halden  1 Menn  F15-19 15-19 år  2020           Personer   
4  3001 Halden  1 Menn  F20-24 20-24 år  2020           Personer   

   07459: Befolkning, etter region, kjønn, alder, år og statistikkvariabel  
0                                                761                        
1                                                888                        
2                                                947                        
3                                               1029                        
4                                               1020

In [101]:
df["rest"], df["age"], df["rest2"] = df["alder"].str.split(" ",2).str
df = df.drop(columns = ["rest", "rest2", "statistikkvariabel", "år", "alder"])

df["aldersgruppe"], df["rest"] = df["age"].str.split("-",1).str
df["aldersgruppe"] = pd.to_numeric(df["aldersgruppe"], errors='coerce')
df = df.drop(columns = ["rest", "age"])

df["Kommunenr"], df["Kommune"] = df["region"].str.split(" ",1).str
df = df.drop(columns="region")

df.head()

kjønn  \
0  1 Menn   
1  1 Menn   
2  1 Menn   
3  1 Menn   
4  1 Menn   

   07459: Befolkning, etter region, kjønn, alder, år og statistikkvariabel  \
0                                                761                         
1                                                888                         
2                                                947                         
3                                               1029                         
4                                               1020                         

   aldersgruppe Kommunenr Kommune  
0             0      3001  Halden  
1             5      3001  Halden  
2            10      3001  Halden  
3            15      3001  Halden  
4            20      3001  Halden

In [102]:
df = df.groupby(["Kommunenr", "Kommune", "aldersgruppe"]).sum().reset_index()
df["aldersgruppe"] = df.apply(lambda x: "over 65" if x["aldersgruppe"] >= 65 else "under 65", axis=1)
df = df.groupby(["Kommunenr", "Kommune", "aldersgruppe"]).sum().reset_index()

df.head()

Kommunenr       Kommune aldersgruppe  \
0      0301  Oslo kommune      over 65   
1      0301  Oslo kommune     under 65   
2      1101     Eigersund      over 65   
3      1101     Eigersund     under 65   
4      1103     Stavanger      over 65   

   07459: Befolkning, etter region, kjønn, alder, år og statistikkvariabel  
0                                              87380                        
1                                             606114                        
2                                               2687                        
3                                              12124                        
4                                              20729

In [103]:
df = df.pivot_table(index=["Kommunenr", "Kommune"], columns=["aldersgruppe"], values="07459: Befolkning, etter region, kjønn, alder, år og statistikkvariabel").reset_index()
df["andel over 65"] = (df["over 65"]/(df["over 65"]+df["under 65"]))*100
df.head()

aldersgruppe Kommunenr       Kommune  over 65  under 65  andel over 65
0                 0301  Oslo kommune    87380    606114      12.599965
1                 1101     Eigersund     2687     12124      18.141922
2                 1103     Stavanger    20729    122845      14.437851
3                 1106     Haugesund     6342     31015      16.976738
4                 1108       Sandnes    10292     69245      12.939890

# tettbebygd strøk

In [104]:
bebyggelse = pd.read_excel("Folkemengde-2.xlsx")
bebyggelse["Kommunenr"], bebyggelse["Kommune"] = bebyggelse["Kommune"].str.split(" ",1).str
bebyggelse["rest"], bebyggelse["Kommunenr"] = bebyggelse["Kommunenr"].str.split("-",1).str
bebyggelse = bebyggelse.drop(columns = ["rest"])

innbyggere = bebyggelse.groupby(["Kommunenr"])["Befolkning"].sum().reset_index()
bebyggelse.head()

Kommune              Type  Befolkning Kommunenr
0  Halden    Tettbygd strøk       27084      3001
1  Halden  Spredtbygd strøk        4043      3001
2  Halden            Ukjent          50      3001
3    Moss    Tettbygd strøk       46901      3002
4    Moss  Spredtbygd strøk        1863      3002

In [105]:
bebyggelse = bebyggelse.pivot_table(index=["Kommunenr", "Kommune"], columns=["Type"], values="Befolkning").reset_index()
bebyggelse["Andel i tettebebyggelse"] = ((bebyggelse["Tettbygd strøk"]/(bebyggelse["Tettbygd strøk"]+bebyggelse["Spredtbygd strøk"]+bebyggelse["Ukjent"])))*100
bebyggelse = bebyggelse.drop(columns = ["Kommune", "Spredtbygd strøk", "Tettbygd strøk", "Ukjent"])
bebyggelse = bebyggelse.merge(innbyggere, how="left", on="Kommunenr")
bebyggelse.head()

Kommunenr  Andel i tettebebyggelse  Befolkning
0      0301                99.422674      681071
1      1101                82.805125       14830
2      1103                95.848881      142034
3      1106                97.535570       37250
4      1108                93.825775       78439

# tilhørighet/mapping

In [106]:
kom = pd.read_csv("kommunetilhorighet_2020.csv", sep=";", decimal=",")
kom.tail()

Fylkesnummer                                              Fylke  \
351            54  Troms og Finnmark - Romsa ja Finnmárku - Troms...   
352            54  Troms og Finnmark - Romsa ja Finnmárku - Troms...   
353            54  Troms og Finnmark - Romsa ja Finnmárku - Troms...   
354            54  Troms og Finnmark - Romsa ja Finnmárku - Troms...   
355            54  Troms og Finnmark - Romsa ja Finnmárku - Troms...   

     Kommunenummer            Kommune  
351           5440           Berlevåg  
352           5441      Deatnu - Tana  
353           5442  Unjárga - Nesseby  
354           5443          Båtsfjord  
355           5444       Sør-Varanger

In [107]:
kom["Fylke"], kom["rest"] = kom["Fylke"].str.split("-",1).str
kom.tail()

Fylkesnummer               Fylke  Kommunenummer            Kommune  \
351            54  Troms og Finnmark            5440           Berlevåg   
352            54  Troms og Finnmark            5441      Deatnu - Tana   
353            54  Troms og Finnmark            5442  Unjárga - Nesseby   
354            54  Troms og Finnmark            5443          Båtsfjord   
355            54  Troms og Finnmark            5444       Sør-Varanger   

                                           rest  
351   Romsa ja Finnmárku - Tromssa ja Finmarkku  
352   Romsa ja Finnmárku - Tromssa ja Finmarkku  
353   Romsa ja Finnmárku - Tromssa ja Finmarkku  
354   Romsa ja Finnmárku - Tromssa ja Finmarkku  
355   Romsa ja Finnmárku - Tromssa ja Finmarkku

# JOIN

In [108]:
data = df.merge(bebyggelse, how="left", on="Kommunenr")
data.head()

Kommunenr       Kommune  over 65  under 65  andel over 65  \
0      0301  Oslo kommune    87380    606114      12.599965   
1      1101     Eigersund     2687     12124      18.141922   
2      1103     Stavanger    20729    122845      14.437851   
3      1106     Haugesund     6342     31015      16.976738   
4      1108       Sandnes    10292     69245      12.939890   

   Andel i tettebebyggelse  Befolkning  
0                99.422674      681071  
1                82.805125       14830  
2                95.848881      142034  
3                97.535570       37250  
4                93.825775       78439

In [109]:
data["Kommunenr"] = pd.to_numeric(data["Kommunenr"], errors='coerce')
data = data.merge(kom, how="left", left_on="Kommunenr", right_on="Kommunenummer")


In [110]:
results, bin_edges = pd.qcut(data['Andel i tettebebyggelse'], q=3, labels=["Lav", "Mid", "Høy"], retbins=True)
bebyggelse_thresh = pd.DataFrame(zip(bin_edges, ["Lav", "Mid", "Høy"]), columns=['Threshold', 'Tekst'])
bebyggelse_thresh

Threshold Tekst
0   0.000000   Lav
1  44.550362   Mid
2  69.745587   Høy

In [111]:
results, bin_edges = pd.qcut(data['andel over 65'], q=3, labels=["Lav", "Mid", "Høy"], retbins=True)
alder_thresh = pd.DataFrame(zip(bin_edges, ["Lav", "Mid", "Høy"]), columns=['Threshold', 'Tekst'])
alder_thresh

Threshold Tekst
0  11.648059   Lav
1  20.087025   Mid
2  23.191483   Høy

In [132]:
legend = [i for i in data["Fylke"].dropna().unique()]
legend.sort()

grey = "rgba(192,192,192,1)"
b = "rgb(9,28,87)"
maroon = "rgb(200,33,72)"

fig = px.scatter(data, 
                 x="Andel i tettebebyggelse", 
                 y="andel over 65", 
                 category_orders={"Fylke": legend},
                 color="Fylke",
                 hover_name="Kommune_x",
                 size="Befolkning",
                 size_max=60,
                 #marginal_x="histogram", marginal_y="histogram",
                 template = "plotly_white",
                 range_x=[-1,110], range_y=[8,35],
                 title = "<b>Potensielt sårbare kommuner i Norge</b><br>Alderssammensetning og tettebebyggelse farget etter tertiler.<br>Datakilde: ssb.no",
                 labels = {"level_1": "Dager siden antall smittede passerte 5", "variable": "Dato", "value": "Totalt registrerte smittede"}    
                )

fig.add_shape(type="rect",
            x0=-1, y0=8,
            x1=110, y1=20.087025,
            line_width=0,layer="below",
            fillcolor=maroon, opacity=0.1,)

fig.add_shape(type="rect",
            x0=-1, y0=20.087025,
            x1=110, y1=23.191483,
            line_width=0,layer="below",
            fillcolor=maroon, opacity=0.4)

fig.add_shape(type="rect",
            x0=-1, y0=23.191483,
            x1=110, y1=35,
            line_width=0,layer="below",
            fillcolor=maroon, opacity=0.7)

#vertical areas:
fig.add_shape(type="rect",
            x0=-1, y0=8,
            x1=44.550362, y1=35,
            line_width=0,layer="below",
            fillcolor=b, opacity=0.1,)

fig.add_shape(type="rect",
            x0=44.550362, y0=8,
            x1=69.745587, y1=35,
            line_width=0,layer="below",
            fillcolor=b, opacity=0.35)

fig.add_shape(type="rect",
            x0=69.745587, y0=8,
            x1=110, y1=35,
            line_width=0,layer="below",
            fillcolor=b, opacity=0.7)

fig.update_layout(
    updatemenus = list([
    dict(type="buttons", 
         direction="left", 
         active=0,
         buttons=list([
                        dict(label='Hele landet',
                 method='update',
                 args=[{'visible': [True, True, True, True, True, True, True, True, True, True, True]}]), 
            dict(label='Midt',
                 method='update',
                 args=[{'visible': [False, False, True, False, False, False, False, True, False, False, False]}]),         
            dict(label='Nord',
                 method='update',
                 args=[{'visible': [False, False, False, True, False, False, True, False, False, False, False]}]),
            
            dict(label='Sør-Øst',
                 method='update',
                 args=[{'visible': [True, True, False, False, True, False, False, False, True, False, True]}]),  
                               
             dict(label='Vest',
                 method='update',
                 args=[{'visible': [False, False, False, False, False, True, False, False, False, True, False]},
                       ])  
             
            ]),
            showactive=True,
            x=0.5,
            xanchor="center",
            y=-0.2,
            yanchor="top"
        )
    ]))

fig.update_layout(autosize=True,
    margin=dict(l=100, r=100, t=120, b=100),
    paper_bgcolor='rgba(0, 0, 0, 0)',
    xaxis=dict(showgrid=False),
    yaxis=dict(showgrid=False),
    #plot_bgcolor='rgb(248, 248, 255),'
                 )

#py.plot(fig, filename='sarbare_kommuner.html', auto_open=False)
fig.show()

# DASH project

In [113]:
import dash
import dash_core_components as dcc
import dash_html_components as html
from dash.dependencies import Input, Output

In [131]:
app = dash.Dash(__name__)
server = app.server
RHF = data.Fylke.unique()
app.layout = html.Div([
    html.Div([dcc.Dropdown(id='valg', options=[{'label': i, 'value': i} for i in RHF],
                           value='Oslo', style={'width': '140px'})]),
    dcc.Graph('shot-dist-graph', config={'displayModeBar': False})])

@app.callback(
    Output('shot-dist-graph', 'figure'),
    [Input('valg', 'value')]
)

def update_graph(grpname):
    import plotly.express as px
    return px.scatter(data[data.Kommune_x == grpname], 
                     x="Andel i tettebebyggelse", 
                     y="andel over 65",
                      size='Befolkning', 
                      color='Fylke')

if __name__ == '__main__':
    app.run_server(debug=False)

 * Serving Flask app "__main__" (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


 * Running on http://127.0.0.1:8050/ (Press CTRL+C to quit)
127.0.0.1 - - [21/Apr/2020 15:16:34] "GET / HTTP/1.1" 200 -
127.0.0.1 - - [21/Apr/2020 15:16:34] "GET /_dash-component-suites/dash_core_components/highlight.pack.js?v=1.3.1&m=1576595950 HTTP/1.1" 200 -
127.0.0.1 - - [21/Apr/2020 15:16:34] "GET /_dash-component-suites/dash_renderer/prop-types@15.7.2.min.js?v=1.1.2&m=1576595738 HTTP/1.1" 200 -
127.0.0.1 - - [21/Apr/2020 15:16:34] "GET /_dash-component-suites/dash_renderer/react@16.8.6.min.js?v=1.1.2&m=1576595738 HTTP/1.1" 200 -
127.0.0.1 - - [21/Apr/2020 15:16:34] "GET /_dash-component-suites/dash_renderer/react-dom@16.8.6.min.js?v=1.1.2&m=1576595738 HTTP/1.1" 200 -
127.0.0.1 - - [21/Apr/2020 15:16:34] "GET /_dash-component-suites/dash_renderer/dash_renderer.min.js?v=1.1.2&m=1576595738 HTTP/1.1" 200 -
127.0.0.1 - - [21/Apr/2020 15:16:34] "GET /_dash-component-suites/dash_core_components/dash_core_components.min.js?v=1.3.1&m=1576595950 HTTP/1.1" 200 -
127.0.0.1 - - [21/Apr/2020 1

Exception on /_dash-update-component [POST]
Traceback (most recent call last):
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 2446, in wsgi_app
    response = self.full_dispatch_request()
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1951, in full_dispatch_request
    rv = self.handle_user_exception(e)
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1820, in handle_user_exception
    reraise(exc_type, exc_value, tb)
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/_compat.py", line 39, in reraise
    raise value
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1949, in full_dispatch_request
    rv = self.dispatch_request()
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1935, in dispatch_request
    return sel

Exception on /_dash-update-component [POST]
Traceback (most recent call last):
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 2446, in wsgi_app
    response = self.full_dispatch_request()
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1951, in full_dispatch_request
    rv = self.handle_user_exception(e)
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1820, in handle_user_exception
    reraise(exc_type, exc_value, tb)
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/_compat.py", line 39, in reraise
    raise value
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1949, in full_dispatch_request
    rv = self.dispatch_request()
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1935, in dispatch_request
    return sel

127.0.0.1 - - [21/Apr/2020 15:16:41] "POST /_dash-update-component HTTP/1.1" 500 -


...

Exception on /_dash-update-component [POST]
Traceback (most recent call last):
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 2446, in wsgi_app
    response = self.full_dispatch_request()
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1951, in full_dispatch_request
    rv = self.handle_user_exception(e)
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1820, in handle_user_exception
    reraise(exc_type, exc_value, tb)
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/_compat.py", line 39, in reraise
    raise value
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1949, in full_dispatch_request
    rv = self.dispatch_request()
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1935, in dispatch_request
    return sel

127.0.0.1 - - [21/Apr/2020 15:17:07] "POST /_dash-update-component HTTP/1.1" 500 -


Exception on /_dash-update-component [POST]
Traceback (most recent call last):
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 2446, in wsgi_app
    response = self.full_dispatch_request()
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1951, in full_dispatch_request
    rv = self.handle_user_exception(e)
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1820, in handle_user_exception
    reraise(exc_type, exc_value, tb)
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/_compat.py", line 39, in reraise
    raise value
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1949, in full_dispatch_request
    rv = self.dispatch_request()
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1935, in dispatch_request
    return sel

Exception on /_dash-update-component [POST]
Traceback (most recent call last):
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 2446, in wsgi_app
    response = self.full_dispatch_request()
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1951, in full_dispatch_request
    rv = self.handle_user_exception(e)
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1820, in handle_user_exception
    reraise(exc_type, exc_value, tb)
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/_compat.py", line 39, in reraise
    raise value
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1949, in full_dispatch_request
    rv = self.dispatch_request()
  File "/Users/familien_nerva-koch/opt/anaconda3/lib/python3.7/site-packages/flask/app.py", line 1935, in dispatch_request
    return sel

127.0.0.1 - - [21/Apr/2020 15:17:09] "POST /_dash-update-component HTTP/1.1" 500 -


In [ ]:
fig = px.scatter(data, 
                 x="Andel i tettebebyggelse", 
                 y="andel over 65", 
                 category_orders={"Fylke": legend},
                 color="Fylke",
                 hover_name="Kommune_x",
                 size="Befolkning",
                 size_max=60,
                 #marginal_x="histogram", marginal_y="histogram",
                 template = "plotly_white",
                 range_x=[-1,110], range_y=[8,35],
                 title = "<b>Potensielt sårbare kommuner i Norge</b><br>Alderssammensetning og tettebebyggelse farget etter tertiler.<br>Datakilde: ssb.no",
                 labels = {"level_1": "Dager siden antall smittede passerte 5", "variable": "Dato", "value": "Totalt registrerte smittede"}    
                )

app = dash.Dash()
app.layout = html.Div([
    dcc.Graph(figure=fig)
])

app.run_server(debug=True, use_reloader=False)

fig.show()

In [130]:
data.head()

Kommunenr     Kommune_x  over 65  under 65  andel over 65  \
0        301  Oslo kommune    87380    606114      12.599965   
1       1101     Eigersund     2687     12124      18.141922   
2       1103     Stavanger    20729    122845      14.437851   
3       1106     Haugesund     6342     31015      16.976738   
4       1108       Sandnes    10292     69245      12.939890   

   Andel i tettebebyggelse  Befolkning  Fylkesnummer     Fylke  Kommunenummer  \
0                99.422674      681071             3      Oslo            301   
1                82.805125       14830            11  Rogaland           1101   
2                95.848881      142034            11  Rogaland           1103   
3                97.535570       37250            11  Rogaland           1106   
4                93.825775       78439            11  Rogaland           1108   

   Kommune_y rest  
0       Oslo  NaN  
1  Eigersund  NaN  
2  Stavanger  NaN  
3  Haugesund  NaN  
4    Sandnes  NaN

In [194]:
data["risk_score"] = (data["andel over 65"] - data["andel over 65"].min())/(data["andel over 65"].max()-data["andel over 65"].min()) * (data["Andel i tettebebyggelse"] - data["Andel i tettebebyggelse"].min())/(data["Andel i tettebebyggelse"].max()-data["Andel i tettebebyggelse"].min())
data.head()

Kommunenr     Kommune_x  over 65  under 65  andel over 65  \
0        301  Oslo kommune    87380    606114      12.599965   
1       1101     Eigersund     2687     12124      18.141922   
2       1103     Stavanger    20729    122845      14.437851   
3       1106     Haugesund     6342     31015      16.976738   
4       1108       Sandnes    10292     69245      12.939890   

   Andel i tettebebyggelse  Befolkning  Fylkesnummer     Fylke  Kommunenummer  \
0                99.422674      681071             3      Oslo            301   
1                82.805125       14830            11  Rogaland           1101   
2                95.848881      142034            11  Rogaland           1103   
3                97.535570       37250            11  Rogaland           1106   
4                93.825775       78439            11  Rogaland           1108   

   Kommune_y rest  risk_score  
0       Oslo  NaN    0.047374  
1  Eigersund  NaN    0.269168  
2  Stavanger  NaN    0.133851  
3  Haugesund  NaN    0.260163  
4    Sandnes  NaN    0.060672

In [97]:
# Create bar plot for trace2
trace2 = []
for q in Types:
    trace2.append(go.Bar(
        x=data.sort_values([q], ascending=False).head(10)[q],
        y=data.sort_values([q], ascending=False).head(10)['Kommune_x'].str.title().tolist(),
        xaxis='x2',
        yaxis='y2',
        visible=False,
        name='Top 10 kommuner {} median price'.format(q),
        orientation='h',
    ))
    
layout.update(updatemenus=list([
    dict(x=0,
         y=1,
         xanchor='left',
         yanchor='middle',
         buttons=list([
             dict(
                 args=['visible', [True, False, False, False]],
                 label='Property type: Unit buy/M',
                 method='restyle'
                 ),
             dict(
                 args=['visible', [False, True, False, False]],
                 label='Property type: Unit rent',
                 method='restyle'
                 ),
             dict(
                 args=['visible', [False, False, True, False]],
                 label='Property type: House rent',
                 method='restyle'
                 ),
             dict(
                 args=['visible', [False, False, False, True]],
                 label='Property type: House buy/M',
                 method='restyle'
                )
            ]),
        )]))
    
trace2[0]['visible'] = True

NameError: name 'Types' is not defined

In [98]:
legend = [i for i in data["Fylke"].dropna().unique()]
legend.sort()

trace = []

for q in Types:
        trace.append(px.scatter(data, 
                 x="Andel i tettebebyggelse", 
                 y="andel over 65", 
                 category_orders={"Fylke": legend},
                 color="Fylke",
                 hover_name="Kommune_x",
                 size="Befolkning",
                 size_max=60,
                 #marginal_x="histogram", marginal_y="histogram",
                 template = "plotly_white",
                 range_x=[-1,110], range_y=[8,35],
                 title = "<b>Potensielt sårbare kommuner i Norge</b><br>Alderssammensetning og tettebebyggelse farget etter tertiler.<br>Datakilde: ssb.no",
                 labels = {"level_1": "Dager siden antall smittede passerte 5", "variable": "Dato", "value": "Totalt registrerte smittede"}    
                )



fig.update_layout(
    updatemenus = list([
    dict(type="buttons", 
         direction="left", 
         active=0,
         buttons=list([
                        dict(label='Hele landet',
                 method='update',
                 args=[{'visible': [True, True, True, True, True, True, True, True, True, True, True]}]), 
            dict(label='Midt',
                 method='update',
                 args=[{'visible': [False, False, True, False, False, False, False, True, False, False, False]}]),         
            dict(label='Nord',
                 method='update',
                 args=[{'visible': [False, False, False, True, False, False, True, False, False, False, False]}]),
            
            dict(label='Sør-Øst',
                 method='update',
                 args=[{'visible': [True, True, False, False, True, False, False, False, True, False, True]}]),  
                               
             dict(label='Vest',
                 method='update',
                 args=[{'visible': [False, False, False, False, False, True, False, False, False, True, False]},
                       ])  
             
            ]),
            showactive=True,
            x=0.5,
            xanchor="center",
            y=-0.2,
            yanchor="top"
        )
    ]))

fig.update_layout(autosize=True,
    margin=dict(l=100, r=100, t=120, b=100),
    paper_bgcolor='rgba(0, 0, 0, 0)',
    xaxis=dict(showgrid=False),
    yaxis=dict(showgrid=False),
    #plot_bgcolor='rgb(248, 248, 255),'
                 )
fig.show()

In [51]:
data.head()

Kommunenr     Kommune_x  over 65  under 65  andel over 65  \
0        301  Oslo kommune    87380    606114      12.599965   
1       1101     Eigersund     2687     12124      18.141922   
2       1103     Stavanger    20729    122845      14.437851   
3       1106     Haugesund     6342     31015      16.976738   
4       1108       Sandnes    10292     69245      12.939890   

   Andel i tettebebyggelse  Befolkning  Fylkesnummer     Fylke  Kommunenummer  \
0                99.422674      681071             3      Oslo            301   
1                82.805125       14830            11  Rogaland           1101   
2                95.848881      142034            11  Rogaland           1103   
3                97.535570       37250            11  Rogaland           1106   
4                93.825775       78439            11  Rogaland           1108   

   Kommune_y rest  
0       Oslo  NaN  
1  Eigersund  NaN  
2  Stavanger  NaN  
3  Haugesund  NaN  
4    Sandnes  NaN

# Kart

In [69]:
import geopandas as gpd
import pandas as pd
from shapely.geometry import LineString, MultiLineString

In [81]:
def shapefile_to_geojson(gdf, index_list, level = 2, tolerance=0.025): 
    # gdf - geopandas dataframe containing the geometry column and values to be mapped to a colorscale
    # index_list - a sublist of list(gdf.index)  or gdf.index  for all data
    # level - int that gives the level in the shapefile
    # tolerance - float parameter to set the Polygon/MultiPolygon degree of simplification
    
    # returns a geojson type dict 
   
    geo_names = list(gdf[f'NAME_{level}'])
    geojson = {'type': 'FeatureCollection', 'features': []}
    for index in index_list:
        geo = gdf['geometry'][index].simplify(tolerance)
    
        if isinstance(geo.boundary, LineString):
            gtype = 'Polygon'
            bcoords = np.dstack(geo.boundary.coords.xy).tolist()
    
        elif isinstance(geo.boundary, MultiLineString):
            gtype = 'MultiPolygon'
            bcoords = []
            for b in geo.boundary:
                x, y = b.coords.xy
                coords = np.dstack((x,y)).tolist() 
                bcoords.append(coords) 
        else: pass
        
        
       
        feature = {'type': 'Feature', 
                   'id' : index,
                   'properties': {'name': geo_names[index]},
                   'geometry': {'type': gtype,
                                'coordinates': bcoords},
                    }
                                
        geojson['features'].append(feature)
    return geojson

In [90]:
import os

graphs = set(os.listdir("/Users/familien_nerva-koch/Documents"))

gdf = geopandas.read_file("/Users/familien_nerva-koch/Documents/Helse-Nord/KommunerKyst/Kommuner2020.shp")
gdf.head()

kommunenum            navn  \
0      5020.0            Osen   
1      5022.0         Rennebu   
2      5021.0          Oppdal   
3      5028.0          Melhus   
4      5027.0  Midtre Gauldal   

                                            geometry  
0  MULTIPOLYGON Z (((269579.990 7137979.000 0.000...  
1  POLYGON Z ((222840.270 6972994.330 0.000, 2228...  
2  POLYGON Z ((203841.430 6950369.520 0.000, 2038...  
3  MULTIPOLYGON Z (((260161.904 7030526.216 0.000...  
4  POLYGON Z ((249316.800 6984449.450 0.000, 2492...

In [92]:
geodf = data.to_crs({'init': 'epsg:4326'})
data.to_file("geojson_norge", driver = "GeoJSON")
with open("geojson_norge") as geofile:
    j_file = json.load(geofile)

AttributeError: 'DataFrame' object has no attribute 'to_crs'

In [78]:
# source: https://gadm.org/download_country_v3.html


gdf = geopandas.read_file("/Users/familien_nerva-koch/Documents/Helse-Nord/choreploth/gadm36_NOR_shp/gadm36_NOR_2.shp", encoding='utf-8')
gdf.head()

GID_0  NAME_0    GID_1    NAME_1 NL_NAME_1      GID_2          NAME_2  \
0   NOR  Norway  NOR.1_1  Akershus      None  NOR.1.1_1              Ås   
1   NOR  Norway  NOR.1_1  Akershus      None  NOR.1.2_1           Asker   
2   NOR  Norway  NOR.1_1  Akershus      None  NOR.1.3_1  Aurskog-Høland   
3   NOR  Norway  NOR.1_1  Akershus      None  NOR.1.4_1           Bærum   
4   NOR  Norway  NOR.1_1  Akershus      None  NOR.1.5_1        Eidsvoll   

  VARNAME_2 NL_NAME_2    TYPE_2     ENGTYPE_2  CC_2    HASC_2  \
0      None      None  Kommuner  Municipality  None  NO.AK.AS   
1      None      None  Kommuner  Municipality  None  NO.AK.AK   
2      None      None  Kommuner  Municipality  None  NO.AK.AH   
3      None      None  Kommuner  Municipality  None  NO.AK.BA   
4      None      None  Kommuner  Municipality  None  NO.AK.EI   

                                            geometry  
0  POLYGON ((10.81795 59.76057, 10.81918 59.75613...  
1  MULTIPOLYGON (((10.50028 59.78319, 10.49600 59...  
2  POLYGON ((11.65070 59.67160, 11.64187 59.67104...  
3  MULTIPOLYGON (((10.58639 59.89375, 10.58583 59...  
4  POLYGON ((11.13745 60.24908, 11.13624 60.25353...

In [83]:
geojsdata = shapefile_to_geojson(gdf, list(gdf.index))
geojsdata["features"][0].keys()

dict_keys(['type', 'id', 'properties', 'geometry'])

In [85]:
fig = go.Figure(data=go.Choropleth(
    geojson=geojsdata,
    locations=data['Kommune_x'], # Spatial coordinates
    z = data["andel over 65"].astype(float), # Data to be color-coded
    colorscale = 'Reds',
    colorbar_title = "Skala",
    text = data['Kommune_x'], #hover text
    autocolorscale = False,
    marker_line_color='white', # line markers between states
    hovertemplate = '<b>Fylke</b>: <b>%{text}</b>'+
                    '<br> <b>Val </b>: %{z}<br>',
))

fig.update_layout(
    title_text = 'OVERSKRIFT<br>(Hover for breakdown)',
    width=750, height=800,
    geo_scope="europe",
)

fig.update_geos(fitbounds="locations", visible=False)

fig.show()

In [86]:
gdf.head()

GID_0  NAME_0    GID_1    NAME_1 NL_NAME_1      GID_2          NAME_2  \
0   NOR  Norway  NOR.1_1  Akershus      None  NOR.1.1_1              Ås   
1   NOR  Norway  NOR.1_1  Akershus      None  NOR.1.2_1           Asker   
2   NOR  Norway  NOR.1_1  Akershus      None  NOR.1.3_1  Aurskog-Høland   
3   NOR  Norway  NOR.1_1  Akershus      None  NOR.1.4_1           Bærum   
4   NOR  Norway  NOR.1_1  Akershus      None  NOR.1.5_1        Eidsvoll   

  VARNAME_2 NL_NAME_2    TYPE_2     ENGTYPE_2  CC_2    HASC_2  \
0      None      None  Kommuner  Municipality  None  NO.AK.AS   
1      None      None  Kommuner  Municipality  None  NO.AK.AK   
2      None      None  Kommuner  Municipality  None  NO.AK.AH   
3      None      None  Kommuner  Municipality  None  NO.AK.BA   
4      None      None  Kommuner  Municipality  None  NO.AK.EI   

                                            geometry  
0  POLYGON ((10.81795 59.76057, 10.81918 59.75613...  
1  MULTIPOLYGON (((10.50028 59.78319, 10.49600 59...  
2  POLYGON ((11.65070 59.67160, 11.64187 59.67104...  
3  MULTIPOLYGON (((10.58639 59.89375, 10.58583 59...  
4  POLYGON ((11.13745 60.24908, 11.13624 60.25353...

In [88]:
gdf.merge(data, how="left", left_on="NAME_2", right_on="Kommune_x")

GID_0  NAME_0     GID_1    NAME_1 NL_NAME_1        GID_2          NAME_2  \
0     NOR  Norway   NOR.1_1  Akershus      None    NOR.1.1_1              Ås   
1     NOR  Norway   NOR.1_1  Akershus      None    NOR.1.2_1           Asker   
2     NOR  Norway   NOR.1_1  Akershus      None    NOR.1.3_1  Aurskog-Høland   
3     NOR  Norway   NOR.1_1  Akershus      None    NOR.1.4_1           Bærum   
4     NOR  Norway   NOR.1_1  Akershus      None    NOR.1.5_1        Eidsvoll   
..    ...     ...       ...       ...       ...          ...             ...   
433   NOR  Norway  NOR.19_1  Vestfold      None  NOR.19.11_1          Stokke   
434   NOR  Norway  NOR.19_1  Vestfold      None  NOR.19.12_1         Svelvik   
435   NOR  Norway  NOR.19_1  Vestfold      None  NOR.19.13_1           Tjøme   
436   NOR  Norway  NOR.19_1  Vestfold      None  NOR.19.14_1        Tønsberg   
437   NOR  Norway  NOR.19_1  Vestfold      None  NOR.19.15_1           Vaale   

    VARNAME_2 NL_NAME_2    TYPE_2  ...  over 65  under 65 andel over 65  \
0        None      None  Kommuner  ...   2900.0   17539.0     14.188561   
1        None      None  Kommuner  ...  15885.0   78556.0     16.820025   
2        None      None  Kommuner  ...   3399.0   13991.0     19.545716   
3        None      None  Kommuner  ...  21244.0  106487.0     16.631828   
4        None      None  Kommuner  ...   4134.0   21302.0     16.252555   
..        ...       ...       ...  ...      ...       ...           ...   
433      None      None  Kommuner  ...      NaN       NaN           NaN   
434      None      None  Kommuner  ...      NaN       NaN           NaN   
435      None      None  Kommuner  ...      NaN       NaN           NaN   
436      None      None  Kommuner  ...  10175.0   46118.0     18.075072   
437      None      None  Kommuner  ...      NaN       NaN           NaN   

    Andel i tettebebyggelse  Befolkning Fylkesnummer                 Fylke  \
0                 84.347185     20335.0         30.0                 Viken   
1                 94.286873     93679.0         30.0                 Viken   
2                 57.328364     17173.0         30.0                 Viken   
3                 98.852895    126841.0         30.0                 Viken   
4                 80.585096     24919.0         30.0                 Viken   
..                      ...         ...          ...                   ...   
433                     NaN         NaN          NaN                   NaN   
434                     NaN         NaN          NaN                   NaN   
435                     NaN         NaN          NaN                   NaN   
436               87.294008     55706.0         38.0  Vestfold og Telemark   
437                     NaN         NaN          NaN                   NaN   

     Kommunenummer       Kommune_y  rest  
0           3021.0              Ås   NaN  
1           3025.0           Asker   NaN  
2           3026.0  Aurskog-Høland   NaN  
3           3024.0           Bærum   NaN  
4           3035.0        Eidsvoll   NaN  
..             ...             ...   ...  
433            NaN             NaN   NaN  
434            NaN             NaN   NaN  
435            NaN             NaN   NaN  
436         3803.0        Tønsberg   NaN  
437            NaN             NaN   NaN  

[438 rows x 26 columns]

In [21]:
counties.head()

AttributeError: 'dict' object has no attribute 'head'